LSE Data Science Institute | ME204 (2023/24) | Week 03 Day 01

# 🗓️ Week 03 – Day 01: Intro to Databases and SQL


<span style="display: inline-block; padding: 0 10px; font-size: 1.15em;line-height: 1.5em; white-space: nowrap; border: 1px solid #3995ba; border-radius: .5em; color: #fcfcfc; background-color: #3995ba; vertical-align: middle;font-weight: 600 !important;">MORNING NOTEBOOK</span>

**DATE:** 22 July 2024

**AUTHOR:** Dr [Jon Cardoso-Silva](https://jonjoncardoso.github.io)

-----


# ⚙️ Setup

You can use your `base` environment or create a new one for this notebook. 

These are the libraries you need to install:

<div style="width:60%;font-size:0.85em">

```bash
pip install pandas numpy lets-plot numerize tqdm sqlalchemy jupysql
```

💡 **NOTE**: There are a few new ones today: the [`jupysql`](https://jupysql.ploomber.io/en/latest/intro.html) and [`sqlalchemy`](https://www.sqlalchemy.org/) packages.

</div>

**IMPORTS:**

In [1]:
import os
import sqlite3


import numpy as np
import pandas as pd

from tqdm.notebook import tqdm, trange
tqdm.pandas()

**CONSTANTS:**

In [2]:
DATA_FOLDER = os.path.join('../data/')

In [3]:
%load_ext sql
%config SqlMagic.autocommit=True # for engines that do not support autommit

# 1. Context

##  💽 What is a database?

At its core, a database is a collection of data stored in a computer system. It's like a structured storage space that allows us to perform various data-related operations, including:

- storing
- retrieving
- modifying, and 
- deleting data.

### Relational databases

The most common type of database is a **relational database**, where data is stored in tables that are related to one another. This allows for easy organization and access to data. Additionally, distributed databases can be replicated across multiple points in a network.

A key feature of relational databases is that they are persistent, meaning the data remains even after a computer crash or power outage.

### Database management systems

We use **database management systems** (DBMS) to interact with databases. These systems serve as intermediaries between users and the databases, enabling operations on the data. 

Some popular examples of DBMS include:

- [MySQL](https://www.mysql.com/)
- [PostgreSQL](https://www.postgresql.org/)
- [SQLite](https://www.sqlite.org/index.html)
- [Microsoft SQL Server](https://www.microsoft.com/en-us/sql-server/sql-server-2019)
- [Oracle Database](https://www.oracle.com/database/)
- [IBM DB2](https://www.ibm.com/analytics/db2)

Database administrators (**DBAs**) are responsible for managing databases. They handle tasks like installing or upgrading the DBMS, troubleshooting issues, and monitoring database performance and security. DBAs also contribute to planning and developing the database structure to cater to users' needs. 

### Database structure

A database consists of tables, each containing rows and columns. Every row represents a set of related data, and all rows in a table have the same structure. For instance, a table about people might have rows for each person, with columns for name, address, phone number, etc. 

_Sounds familiar?_ That is because the tidy data principles were inspired by relational databases, and `pandas` embraces this relational approachin several ways.

Now, while diving deep into database theory could be a course on its own, we'll focus on hands-on applications. We will set up a simple database, populate it with data, and query it using SQL -- all while taking notes of similarities and differences with `pandas`.

By the way, databases are typically stored on a **server**, sometimes in multiple ones to allow for:
- **load balancing:** if the database or queries are too heavy for a single server, the load can be distributed and processed by multiple servers.
- **fault tolerance:** if one server fails, the others can take over to ensure the database remains accessible.

-----

# 2. Setting up a SQLite database

For our purposes, we'll use a **local database** stored on our computer. 

We'll use [SQLite](https://www.sqlite.org/index.html), a lightweight database that doesn't require a server to run. 

[👉 SQLite databases are stored in a single file, typically with the extension `.db` or `.sqlite`. Different to a CSV file, however, a SQLite file can store multiple tables (multiple data frames), and we can use the same SQL language one would use on a powerful database to query it.]{style="display:inline-block;margin-left:2em;font-size:0.90em;"}

## 2.1 Using pure Python directly (not recommended in this course)

Python has a built-in module called `sqlite3` that allows us to interact with SQLite databases. Below are some commands you can use to create a database, create a table, insert data, and query data.


**Create a database:**

In [18]:
# Create a SQLite database in the ../data/ directory if it does not already exist
conn = sqlite3.connect(os.path.join(DATA_FOLDER, './supermarket.db'))

[👈 If you look at your files here on VS Code. You should see a new file called `supermarket.db` alongside the file that represents this notebook.]{style="display:inline-block;margin-left:2em;width:60%;font-size:0.9em}

[⚠️ **WARNING**: You now have an open connection to the database. If you try to delete the file, you'll get an error because the connection is still open. The connection will remain active while you have this Python kernel running. To close the connection, use the `conn.close()` method or shutdown/restart the kernel.]{style="display:inline-block;margin-left:2em;width:60%;font-size:0.9em"}


**Create a table:**

Tables are like data frames in `pandas`, they are rectangular structures with rows and columns. Each row represents a record (presumably each row is a unique entity) and each column represents a field (a piece of information about the entity).

In [9]:
# Create our first table based on the Waitrose data we have

conn.execute('''
CREATE TABLE IF NOT EXISTS product_listing (
    id INTEGER PRIMARY KEY,
    offer BOOLEAN,
    image_url TEXT,
    page TEXT,
    name TEXT,
    size TEXT,
    item_price TEXT,
    price_per_unit TEXT,
    offer_description TEXT,
    category TEXT
)
''')


Different to `pandas`, in a RDBMS we **MUST** specify all the columns and all their data types **BEFORE** inserting any data.

We call this specification, the **schema** of the table.

**Check that the table was created:**

In [10]:
# Inside the database, there is always an internal table called sqlite_master that stores the schema of the database.
conn.execute('''
SELECT name FROM sqlite_master WHERE type='table';
''').fetchall()

[('product_listing',)]

[💡 **TIP:** The string above is a **SQL Query**. SQL stands for **Structured Query Language** and is the language used to interact with relational databases. As with popular languages, SQL has its own syntax and keywords.]{style="display:inline-block;margin-left:2em;width:60%;font-size:0.9em"}

👉 Check out the [W3 Schools SQL Syntax](https://www.w3schools.com/sql/sql_syntax.asp) page for a quick reference.

**Add a record to the table:**

Suppose we want to add the following record to the `products` table:

<div style="font-size:0.75em">

```json
{
 'id': 525635,
 'offer': False,
 'image-url': 'https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_525635_BP_3.jpg',
 'page': 'https://www.waitrose.com/ecom/products/organix-raspberry-apple-soft-oaty-bars/525635-812878-812879',
 'name': 'Organix Raspberry & Apple Soft Oaty Bars',
 'size': '6x23g',
 'item-price': '£3.15',
 'price-per-unit': '£2.29/100g',
 'offer-description': nan,
 'category': 'Baby, Child & Parent'
}
```

</div>

This is how the SQL INSERT statement looks like:


In [47]:
conn.execute('''
INSERT INTO product_listing (id, offer, image_url, page, name, size, item_price, price_per_unit, offer_description, category)
VALUES (525635, 
        0, 
        "https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_525635_BP_3.jpg", 
        "https://www.waitrose.com/ecom/products/organix-raspberry-apple-soft-oaty-bars/525635-812878-812879", 
        "Organix Raspberry & Apple Soft Oaty Bars", "6x23g", "£3.15", "£2.29/100g", NULL, "Baby, Child & Parent"
);
''')

<div style="font-size:0.75em;width:70%">

💡 **IMPORTANT:** If you try to run the code cell above again, you will likely get the following error:

```python
IntegrityError: UNIQUE constraint failed: product_listing.id
```

This is because we configured the `id` column as a **primary key**. This means that the values in this column **MUST** be unique. If you try to insert a record with an `id` that already exists in the table, you'll get an error. This is a very good thing, as it helps to ensure data integrity! 

It does not have to be just the `id` column, you get to set what column or columns are the primary key when you create the table.

</div>

**Reading data from a SQLite database**

In [48]:
# SELECT * returns all columns and all rows from the table
conn.execute('''
SELECT * FROM product_listing;
''').fetchall()

[(525635,
  0,
  'https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_525635_BP_3.jpg',
  'https://www.waitrose.com/ecom/products/organix-raspberry-apple-soft-oaty-bars/525635-812878-812879',
  'Organix Raspberry & Apple Soft Oaty Bars',
  '6x23g',
  '£3.15',
  '£2.29/100g',
  None,
  'Baby, Child & Parent')]

**Deleting and recreating the table:**

Say you made a mistake and you want to delete the table and recreate it. You can do this with the following SQL command:


In [49]:
# Delete the product_listing table
conn.execute('''
DROP TABLE product_listing;
''')

In [19]:
# I want the triplet (name, id, size) to be the primary key of the table
conn.execute('''
CREATE TABLE IF NOT EXISTS product_listing (
    id INTEGER,
    offer BOOLEAN,
    image_url TEXT,
    page TEXT,
    name TEXT,
    size TEXT,
    item_price TEXT,
    price_per_unit TEXT,
    offer_description TEXT,
    category TEXT,
    PRIMARY KEY (name, id, size) -- This is the primary key
)
''')

# Add the same product to the table again
conn.execute('''
INSERT INTO product_listing (id, offer, image_url, page, name, size, item_price, price_per_unit, offer_description, category)
VALUES (525635, 
        0, 
        "https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_525635_BP_3.jpg", 
        "https://www.waitrose.com/ecom/products/organix-raspberry-apple-soft-oaty-bars/525635-812878-812879", 
        "Organix Raspberry & Apple Soft Oaty Bars", "6x23g", "£3.15", "£2.29/100g", NULL, "Baby, Child & Parent"
);
''')

# Select all columns and all rows from the table
conn.execute('''
SELECT * FROM product_listing;
''').fetchall()

[(525635,
  0,
  'https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_525635_BP_3.jpg',
  'https://www.waitrose.com/ecom/products/organix-raspberry-apple-soft-oaty-bars/525635-812878-812879',
  'Organix Raspberry & Apple Soft Oaty Bars',
  '6x23g',
  '£3.15',
  '£2.29/100g',
  None,
  'Baby, Child & Parent')]

In [20]:
conn.commit() # Commit the transaction or else the changes will be lost after the connection is closed

There are many other SQL commands you can use to interact with this database, such as:

- `UPDATE`: to update records that already exist
- `DELETE`: to remove records
- `CREATE INDEX`: to create an index on a table (to speed up complex queries)
- `DROP INDEX`: to remove an index
- `ALTER TABLE`: to modify the structure/schema of a table
- `CREATE VIEW`: to create a virtual table based on the result of a query (!)


**Let's close the connection and show you a better way to interact with SQLite databases in Python from Jupyter notebooks.**

In [21]:
conn.close()

## 2.2 Reading directly into a pandas DataFrame (recommended)

In [ ]:
# Pandas require an active connection
conn = sqlite3.connect(os.path.join(DATA_FOLDER, 'supermarket.db'))

# Load the data from the product_listing table into a pandas DataFrame
df = pd.read_sql_query('''
SELECT * FROM product_listing;
''', conn)

In [26]:
# Now you are back to using pandas
df

id  offer                                          image_url  \
0  525635      0  https://ecom-su-static-prod.wtrecom.com/images...   

                                                page  \
0  https://www.waitrose.com/ecom/products/organix...   

                                       name   size item_price price_per_unit  \
0  Organix Raspberry & Apple Soft Oaty Bars  6x23g      £3.15     £2.29/100g   

  offer_description              category  
0              None  Baby, Child & Parent

**Decide what to load from the database:**

In [28]:
df = pd.read_sql_query('''
SELECT id, name, size, category, item_price from product_listing
''', conn)

df

id                                      name   size  \
0  525635  Organix Raspberry & Apple Soft Oaty Bars  6x23g   

               category item_price  
0  Baby, Child & Parent      £3.15

You can do pretty much all the things you already know how to do with `pandas` DataFrames, but with the added benefit of using SQL (faster) to query the data.

**Copy an entire CSV file into a table**

In [4]:
# Run this very long and ugly cell to get the full dataset
all_files = [os.path.join(DATA_FOLDER,  file) for file in os.listdir(DATA_FOLDER) 
             if file.endswith('.csv')]

# Reads every individual file and concatenates them into a single DataFrame using pandas concat
df = pd.concat((pd.read_csv(file) for file in all_files))

df = df.drop_duplicates()

df = df.drop(columns=['data-product-name'])
df = (
    df.rename(columns={
        'data-product-type': 'type',
        'data-product-index': 'index',
        'data-product-id': 'id',
        'data-product-on-offer': 'on-offer',
        'product-page': 'page',
        'product-name': 'name',
        'product-size': 'size',
    })
)

def clean_item_price(item_price: str):
    """
    Cleans the item price string by performing necessary transformations.

    Parameters:
    item_price (str): The item price as a string.

    Returns:
    float: The cleaned item price.
    """
    if pd.isna(item_price):
        return np.nan
    
    item_price = item_price.replace(' each est.', '')
    
   
    if '-' in item_price:
        item_prices = item_price.replace('£', '').split('-')
        item_prices = [float(price) for price in item_prices]
        item_price = np.mean(item_prices)
    else:
        if '£' in item_price:
            item_price = item_price.replace('£', '')
            item_price = float(item_price)
        elif 'p' in item_price:
            item_price = item_price.replace('p', '')
            item_price = float('0.' + item_price)
    
    return float(item_price)

df['id'] = df['id'].astype('int32')
df['cleaned-item-price'] = df['item-price'].apply(lambda price: clean_item_price(price))

selected_rows = df['item-price'].astype(str).str.contains('-')

# The 'size' column of the selected rows all have the same kind of format: (2.2kg-2.8kg).
df.loc[selected_rows, 'size'] = df.loc[selected_rows, 'size'].str.split('-').str[0].str.replace('(', '')

df['item-price'] = df['cleaned-item-price']
df.drop(columns=['cleaned-item-price'], inplace=True)

df

id type  on-offer   index  \
0     525635    G     False     1.0   
1     557746    G     False     2.0   
2      32062    G     False   394.0   
3     767801    G     False     4.0   
4     514054    G     False     5.0   
...      ...  ...       ...     ...   
1589   18427    G     False  1590.0   
1590   11606    G     False  1591.0   
1591    6903    G     False  1592.0   
1592    6125    G     False  1593.0   
1593  707668    W     False  1594.0   

                                              image-url  \
0     https://ecom-su-static-prod.wtrecom.com/images...   
1     https://ecom-su-static-prod.wtrecom.com/images...   
2     https://ecom-su-static-prod.wtrecom.com/images...   
3     https://ecom-su-static-prod.wtrecom.com/images...   
4     https://ecom-su-static-prod.wtrecom.com/images...   
...                                                 ...   
1589  https://ecom-su-static-prod.wtrecom.com/images...   
1590  https://ecom-su-static-prod.wtrecom.com/images...   
1591  https://ecom-su-static-prod.wtrecom.com/images...   
1592  https://ecom-su-static-prod.wtrecom.com/images...   
1593  https://ecom-su-static-prod.wtrecom.com/images...   

                                                   page  \
0     https://www.waitrose.com/ecom/products/organix...   
1     https://www.waitrose.com/ecom/products/organix...   
2     https://www.waitrose.com/ecom/products/aptamil...   
3     https://www.waitrose.com/ecom/products/essenti...   
4     https://www.waitrose.com/ecom/products/organix...   
...                                                 ...   
1589  https://www.waitrose.com/ecom/products/duchy-o...   
1590  https://www.waitrose.com/ecom/products/cooks-i...   
1591  https://www.waitrose.com/ecom/products/no-1-ba...   
1592  https://www.waitrose.com/ecom/products/cooks-i...   
1593  https://www.waitrose.com/ecom/products/duchy-o...   

                                                   name  \
0              Organix Raspberry & Apple Soft Oaty Bars   
1                         Organix Carrot Cake Oaty Bars   
2                              Aptamil 2 Follow On Milk   
3                                  Essential Baby Wipes   
4                              Organix Apple Rice Cakes   
...                                                 ...   
1589                Duchy Organic British Lamb Half Leg   
1590                         Cooks' Ingredients Wok Oil   
1591  No. 1 Badoz Vacherin Du Haut-Doubs AOP French ...   
1592                  Cooks' Ingredients White Marzipan   
1593              Duchy Organic Pinot Grigio Bag in Box   

                       size  item-price price-per-unit offer-description  \
0                     6x23g        3.15     £2.29/100g               NaN   
1                     6x23g        3.15     £2.29/100g               NaN   
2                      800g       13.50      £16.88/kg               NaN   
3                       80s        0.95      1.2p each               NaN   
4                       40g        1.60        £4/100g               NaN   
...                     ...         ...            ...               ...   
1589  Typical weight 0.94kg       24.31      £26.00/kg               NaN   
1590                  250ml        2.40      96p/100ml               NaN   
1591                   350g       10.00      £28.58/kg               NaN   
1592                   500g        2.50          £5/kg               NaN   
1593                  2.25L       21.49     £7.17/75cl               NaN   

                  category  
0     Baby, Child & Parent  
1     Baby, Child & Parent  
2     Baby, Child & Parent  
3     Baby, Child & Parent  
4     Baby, Child & Parent  
...                    ...  
1589       Waitrose Brands  
1590       Waitrose Brands  
1591       Waitrose Brands  
1592       Waitrose Brands  
1593       Waitrose Brands  

[25378 rows x 12 columns]

Now here is how you copy that to the database:

In [47]:
df.to_sql('product_listing', conn, if_exists='replace', index=False)

25378

### 2.2.1 You can do group-by operations in SQL too!

(In reality, this feature first appeared in SQL and was later implemented in `pandas`.)

In [63]:
pd.read_sql_query('''
SELECT 
    name,
    size,
    id,
    `item-price` AS price,
    `price-per-unit` AS unit_price,
    -- LIST ALL UNIQUE CATEGORIES
    GROUP_CONCAT(DISTINCT(category)) AS categories
FROM product_listing
WHERE 
    name IS NOT NULL AND
    size IS NOT NULL AND
    -- NAME DOES NOT START WITH A NUMBER
    NOT name GLOB '[0-9]*'
GROUP BY name, size, id
ORDER BY name
''', conn)

name   size      id  price  \
0                                     A Game of Lies   each  930896   6.99   
1                                   A Huge Thank You      1  520065   3.75   
2               A. A. Badenhorst Curator White Blend   75cl  433357   9.99   
3                          A.Vogel Echinaforce Drops  100ml   48215  17.00   
4                        A.Vogel Echinaforce Tablets   120s   33798  11.00   
...                                              ...    ...     ...    ...   
15908        £100,000 a Month for a Year Scratchcard   Each  434887   5.00   
15909        Öpso Japanese Sakura Tree Reed Diffuser   50ml  853904   9.00   
15910  Öpso Mediterranean Citrus Grove Reed Diffuser   50ml  600132   9.00   
15911         Öpso Nordic Birch Forest Reed Diffuser   50ml  583549   9.00   
15912             Ürziger Würzgarten Kabinett Loosen   75cl   47615  15.99   

        unit_price                                       categories  
0       £6.99 each                                             Home  
1             None                                             Home  
2       £9.99/75cl             Beer, Wine & Spirits,Fresh & Chilled  
3        £17/100ml  Dietary & Lifestyle,Toiletries, Health & Beauty  
4        9.2p each  Dietary & Lifestyle,Toiletries, Health & Beauty  
...            ...                                              ...  
15908         None                                             Home  
15909    £18/100ml                                   Home,Household  
15910    £18/100ml                                   Home,Household  
15911    £18/100ml                                   Home,Household  
15912  £15.99/75cl             Beer, Wine & Spirits,Fresh & Chilled  

[15913 rows x 6 columns]

**Should we do a group-by operation in SQL or in `pandas`?**

- If the data is already in a database, it is usually MUCH faster to do it in SQL.
- If you don't have a lot of RAM, it is usually better to do it in SQL. Only the result of the group-by operation will be loaded into the memory of your Python kernel.
- If SQL does not support the type of operations you need to do, then you have no choice but to do it in `pandas`. For example: if you need to run a machine learning model to decide the value of a new column based on the values of other columns, you will need to do it in `pandas`.
- If you are more comfortable with Pandas, then do it in Pandas!


SQL supports some text operations, but it is not as powerful as Python. Always check if the operation you need is supported by SQL before deciding where to do it.

In [65]:
conn.close()

## 2.3 Using the `%sql` magic command (recommended for learning SQL)

Yet another alternative is to use just SQL but via a more user-friendly interface. The `jupysql` package provides a Jupyter magic command that allows us to interact with SQLite databases directly from Jupyter notebooks. This is a more user-friendly way to work with databases in Python.

This is how you establish a connection to the database and give it a name:

In [5]:
%sql sqlite:///../data/supermarket.db --alias supermarket

Connecting to 'supermarket'

Now you can run SQL queries directly in the notebook using the `%%sql` magic command.

In [67]:
%%sql supermarket

-- The syntax highlighting (the colours you get here) look nicer too
SELECT name FROM sqlite_master WHERE type='table';

+-----------------+
|       name      |
+-----------------+
| product_listing |
+-----------------+

In [73]:
%%sql supermarket

SELECT * FROM product_listing ORDER BY `item-price` DESC LIMIT 5;

+--------+------+----------+--------+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+--------------------------------------------------+------+------------+----------------+-------------------+----------------------+
|   id   | type | on-offer | index  |                                                                               image-url                                                                               |                                                                                                                 page                                                                                                                |                       name                       | size | item-price | price-per-unit | offer-description |       category       |
+--------+------+----------+--------+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+--------------------------------------------------+------+------------+----------------+-------------------+----------------------+
| 17830  |  W   |    0     | 1522.0 | <a href=https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_017830_BP_3.jpg>https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_017830_BP_3.jpg</a> |            <a href=https://www.waitrose.com/ecom/products/louis-roederer-cristal-vintage-champagne/017830-8640-8641>https://www.waitrose.com/ecom/products/louis-roederer-cristal-vintage-champagne/017830-8640-8641</a>            |     Louis Roederer Cristal Vintage Champagne     | 75cl |   299.99   |  £299.99/75cl  |        None       | Beer, Wine & Spirits |
| 82418  |  W   |    0     | 1458.0 | <a href=https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_082418_BP_3.jpg>https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_082418_BP_3.jpg</a> |                                      <a href=https://www.waitrose.com/ecom/products/dom-perignon/082418-41929-41930>https://www.waitrose.com/ecom/products/dom-perignon/082418-41929-41930</a>                                      |                   Dom Perignon                   | 75cl |   199.99   |  £199.99/75cl  |        None       | Beer, Wine & Spirits |
| 574495 |  E   |    0     | 303.0  | <a href=https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_574495_BP_3.jpg>https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_574495_BP_3.jpg</a> | <a href=https://www.waitrose.com/ecom/products/no1-30-day-dry-aged-jubilee-rib-of-british-beef/574495-215983-215984>https://www.waitrose.com/ecom/products/no1-30-day-dry-aged-jubilee-rib-of-british-beef/574495-215983-215984</a> | No.1 30 Day Dry Aged Jubilee Rib of British Beef | 6kg  |   182.0    |    £28 / kg    |        None       |   Best of British    |
| 574495 |  E   |    0     | 3434.0 | <a href=https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_574495_BP_3.jpg>https://ecom-su-static-prod.wtrecom.com/images/products/3/LN_574495_BP_3.jpg</a> | <a href=https://www.waitrose.com/ecom/products/no1-30-day-dry-aged-jubilee-rib-of-british-beef/574495-215983-215984>https://www.waitrose.com/ecom/products/no1-30-day-dry-aged-jubilee-rib-of-british-beef/574495-215983-215984</a> | No.1 30 Day Dry Aged Jubilee Rib of British Beef | 6kg  |   182.0    |    £28 / kg    |        None       |   Fresh & Chilled    |
| 574495 |  E   |    0     | 13

**Save it to a pandas DataFrame:**

In [85]:
%%sql --alias supermarket my_df <<

SELECT * FROM product_listing ORDER BY `item-price` DESC LIMIT 5;

Running query in 'supermarket'

In [86]:
type(my_df)

sql.run.resultset.ResultSet

In [87]:
my_df = my_df.DataFrame() # Convert to pandas DataFrame
type(my_df)

pandas.core.frame.DataFrame

In [88]:
my_df

id type  on-offer   index  \
0   17830    W         0  1522.0   
1   82418    W         0  1458.0   
2  574495    E         0   303.0   
3  574495    E         0  3434.0   
4  574495    E         0  1358.0   

                                           image-url  \
0  https://ecom-su-static-prod.wtrecom.com/images...   
1  https://ecom-su-static-prod.wtrecom.com/images...   
2  https://ecom-su-static-prod.wtrecom.com/images...   
3  https://ecom-su-static-prod.wtrecom.com/images...   
4  https://ecom-su-static-prod.wtrecom.com/images...   

                                                page  \
0  https://www.waitrose.com/ecom/products/louis-r...   
1  https://www.waitrose.com/ecom/products/dom-per...   
2  https://www.waitrose.com/ecom/products/no1-30-...   
3  https://www.waitrose.com/ecom/products/no1-30-...   
4  https://www.waitrose.com/ecom/products/no1-30-...   

                                               name  size  item-price  \
0          Louis Roederer Cristal Vintage Champagne  75cl      299.99   
1                                      Dom Perignon  75cl      199.99   
2  No.1 30 Day Dry Aged Jubilee Rib of British Beef   6kg      182.00   
3  No.1 30 Day Dry Aged Jubilee Rib of British Beef   6kg      182.00   
4  No.1 30 Day Dry Aged Jubilee Rib of British Beef   6kg      182.00   

  price-per-unit offer-description              category  
0   £299.99/75cl              None  Beer, Wine & Spirits  
1   £199.99/75cl              None  Beer, Wine & Spirits  
2       £28 / kg              None       Best of British  
3       £28 / kg              None       Fresh & Chilled  
4       £28 / kg              None                Summer

# 3. Multiple tables

First let me draw your attention to a **SQLite limitation:**

SQLite does not support [LIST COLUMNS](https://sqlite.org/datatype3.html). This means that you cannot have a column that contains a list of values. If you need to store a list of values in a column, you will need to create a new table to store the list and link it to the original table using a foreign key.

## 3.1 Two tables solution: `products` and `categories`

Imagine we have a `products` table that **points to** a `categories` table. This is a **one-to-many relationship**. The product table would have a column called `category_id` that would be a foreign key to the `categories` table.

| product_id | product_name | category_id |
|------------|--------------|-------------|
| 1          | Product A    | 1           |
| 2          | Product B    | 2           |
| 3          | Product C    | 1           |
| 4          | Product D    | 3           |
| 5          | Product E    | 2           |

The `categories` table, on the other hand, would look like this:

| category_id | category_name |
|-------------|---------------|
| 1           | Category A    |
| 2           | Category B    |
| 3           | Category C    |


**Recreate the tables:**

In [7]:
df.columns

Index(['id', 'type', 'on-offer', 'index', 'image-url', 'page', 'name', 'size',
       'item-price', 'price-per-unit', 'offer-description', 'category'],
      dtype='object')

In [8]:
%%sql --alias supermarket

DROP TABLE IF EXISTS product_listing;


CREATE TABLE categories
(
    id INTEGER,
    name TEXT,
    PRIMARY KEY (id)
);

CREATE TABLE products
(
    id INTEGER,
    type TEXT,
    `on-offer` BOOLEAN,
    `image-url` TEXT,
    `page` TEXT,
    name TEXT,
    size TEXT,
    `item-price` REAL,
    `price-per-unit` VARCHAR(20),
    `offer-description` TEXT,
    category INTEGER,
    PRIMARY KEY (id, name, size)
    FOREIGN KEY (category) REFERENCES categories(id)
);

Running query in 'supermarket'

++
||
++
++

**We would need to build the `categories` table first:**

In [23]:
table_categories = pd.DataFrame({'id': range(df['category'].nunique()), 'name': df['category'].unique()})
table_categories

id                         name
0    0         Baby, Child & Parent
1    1                       Bakery
2    2         Beer, Wine & Spirits
3    3              Best of British
4    4          Dietary & Lifestyle
5    5               Everyday Value
6    6                Food Cupboard
7    7              Fresh & Chilled
8    8                       Frozen
9    9                         Home
10  10                    Household
11  11                          New
12  12                 Organic Shop
13  13                          Pet
14  14                       Summer
15  15    Tea, Coffee & Soft Drinks
16  16  Toiletries, Health & Beauty
17  17              Waitrose Brands

In [39]:
table_categories.to_sql('categories', conn, if_exists='replace', index=False)

18

In [28]:
# Replace category column in the df DataFrame with the id from the category table

conn = sqlite3.connect(os.path.join(DATA_FOLDER, 'supermarket.db'))

(
    pd.merge(df, table_categories,
             left_on='category', 
             right_on='name', 
             how='left', 
             suffixes=['', '_y'])
      .assign(category=lambda df: df['id_y'])
      .drop(columns=['name_y', 'id_y'])
).to_sql('products', conn, if_exists='replace', index=False)



25378

**List the schemas:**

In [30]:
%%sql --alias supermarket

SELECT * FROM sqlite_master WHERE type='table';

Running query in 'supermarket'

+-------+------------+------------+----------+-----------------------------+
|  type |    name    |  tbl_name  | rootpage |             sql             |
+-------+------------+------------+----------+-----------------------------+
| table | categories | categories |    2     |   CREATE TABLE categories   |
|       |            |            |          |              (              |
|       |            |            |          |           id INTEGER,       |
|       |            |            |          |            name TEXT,       |
|       |            |            |          |         PRIMARY KEY (id)    |
|       |            |            |          |              )              |
| table |  products  |  products  |   1021   |  CREATE TABLE "products" (  |
|       |            |            |          |        "id" INTEGER,        |
|       |            |            |          |          "type" TEXT,       |
|       |            |            |          |      "on-offer" INTEGER,    |
|       |            |            |          |         "index" REAL,       |
|       |            |            |          |       "image-url" TEXT,     |
|       |            |            |          |          "page" TEXT,       |
|       |            |            |          |          "name" TEXT,       |
|       |            |            |          |          "size" TEXT,       |
|       |            |            |          |       "item-price" REAL,    |
|       |            |            |          |     "price-per-unit" TEXT,  |
|       |            |            |          |   "offer-description" TEXT, |
|       |            |            |          |       "category" INTEGER    |
|       |            |            |          |              )              |
+-------+------------+------------+----------+-----------------------------+

**Read just the products table:**

In [33]:
%%sql supermarket

-- READ JUST THE PRODUCTS TABLE
SELECT 
    name,
    size,
    id,
    `item-price` AS price,
    `price-per-unit` AS unit_price,
    -- LIST ALL UNIQUE CATEGORIES
    GROUP_CONCAT(DISTINCT(category)) AS categories
FROM products
WHERE 
    name IS NOT NULL AND
    size IS NOT NULL AND
    -- NAME DOES NOT START WITH A NUMBER
    NOT name GLOB '[0-9]*'
GROUP BY name, size, id
ORDER BY price DESC
LIMIT 5;

+--------------------------------------------------+-----------+--------+--------+--------------+------------+
|                       name                       |    size   |   id   | price  |  unit_price  | categories |
+--------------------------------------------------+-----------+--------+--------+--------------+------------+
|     Louis Roederer Cristal Vintage Champagne     |    75cl   | 17830  | 299.99 | £299.99/75cl |     2      |
|                   Dom Perignon                   |    75cl   | 82418  | 199.99 | £199.99/75cl |     2      |
| No.1 30 Day Dry Aged Jubilee Rib of British Beef |    6kg    | 574495 | 182.0  |   £28 / kg   |   3,7,14   |
|         Oral-B Pro 3 3900 Duo Black/Pink         |    Each   | 610282 | 168.0  |  £168 each   |     16     |
|             Marlboro Gold KS TT 200s             | 10x20Each | 634882 | 159.0  |  79.5p each  |     9      |
+--------------------------------------------------+-----------+--------+--------+--------------+------------+

**Bring the category names into the products table:**

In [44]:
%%sql supermarket

-- LEFT JOIN
SELECT 
    p.name,
    p.size,
    p.id,
    p.`item-price` as price,
    p.`price-per-unit` as unit_price,
    GROUP_CONCAT(DISTINCT c.name) AS categories
FROM products AS p
LEFT JOIN categories AS c
ON p.category = c.id
WHERE 
    p.name IS NOT NULL AND
    p.size IS NOT NULL AND
    -- NAME DOES NOT START WITH A NUMBER
    NOT p.name GLOB '[0-9]*'
GROUP BY p.name, p.size, p.id
ORDER BY price DESC
LIMIT 5;

+--------------------------------------------------+-----------+--------+--------+--------------+----------------------------------------+
|                       name                       |    size   |   id   | price  |  unit_price  |               categories               |
+--------------------------------------------------+-----------+--------+--------+--------------+----------------------------------------+
|     Louis Roederer Cristal Vintage Champagne     |    75cl   | 17830  | 299.99 | £299.99/75cl |          Beer, Wine & Spirits          |
|                   Dom Perignon                   |    75cl   | 82418  | 199.99 | £199.99/75cl |          Beer, Wine & Spirits          |
| No.1 30 Day Dry Aged Jubilee Rib of British Beef |    6kg    | 574495 | 182.0  |   £28 / kg   | Best of British,Fresh & Chilled,Summer |
|         Oral-B Pro 3 3900 Duo Black/Pink         |    Each   | 610282 | 168.0  |  £168 each   |      Toiletries, Health & Beauty       |
|             Marlboro Gold KS TT 200s             | 10x20Each | 634882 | 159.0  |  79.5p each  |                  Home                  |
+--------------------------------------------------+-----------+--------+--------+--------------+----------------------------------------+

----

# 4. PRACTICE!

Let's go a bit over the top and create a more complex database with multiple tables and relationships.

🎯 **ACTION POINTS**

- Create a `supermarket.db` database with the following tables:
    - `products`
    - `categories`
    - `prices`
    - `offers`

- Move the relevant columns to their respective tables and establish the relationships between them.

- Do not add empty offers to the `offers` table. If a product is not on offer, it should simply not have a link from the `products` table to the `offers` table.

- Create a query that retrieves the following columns:
    - `product_name`
    - `category_name`
    - `price`
    - `unit_price`